In [1]:
!pip install faiss-gpu-cu11 --index-url https://pypi.org/simple


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 3.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.1/48.1 MB 17.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 56.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 417.9/417.9 MB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 875.6/875.6 kB 39.7 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
thinc 8.3.6 requires numpy<3.0.0,>=2.0.0, but you have numpy 1.26.4 which is incompatible.
opencv-contrib-python 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 1.26.4 which is incompatible.
opencv-python 4.12.0.88 requires numpy<2.3.0,>=2; pytho

In [1]:
import faiss
print("FAISS version:", faiss.__version__)
print("GPU available:", faiss.get_num_gpus())


import faiss
print(faiss.get_num_gpus())  # should be >=1


FAISS version: 1.12.0
GPU available: 1
1


In [2]:
!pip install -U transformers==4.44.2
!pip install -U sentence-transformers==2.7.0


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 45.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 48.7 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.22.0
    Uninstalling tokenizers-0.22.0:
      Successfully uninstalled tokenizers-0.22.0
  Attempting uninstall: transformers
    Found existing installation: transformers 4.56.1
    Uninstalling transformers-4.56.1:
      Successfully uninstalled transformers-4.56.1
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 171.5/171.5 kB 4.3 MB/s eta 0:00:00
  Attempting uninstall: sentence-transformers
    Found existing installation: sentence-transformers 5.1.0
    Uninstalling sentence-transformers-5.1.0:
      Successfully uninstalled sentence-transformers-5.1.0


In [3]:
# ===================================
# Imports
# ===================================
import os
import torch
import pandas as pd
import numpy as np
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
import faiss
from diffusers import StableDiffusionPipeline, EulerDiscreteScheduler
from google.colab import drive

# ===================================
# Mount Drive
# ===================================
drive.mount('/content/drive', force_remount=True)

# ===================================
# Setup
# ===================================
device = "cuda" if torch.cuda.is_available() else "cpu"
print("⚡ Using device:", device)

base_path = "/content/drive/MyDrive/MediaEval/newsimages_25_v1.1/"
results_dir = os.path.join(base_path, "results_local/")
os.makedirs(results_dir, exist_ok=True)
generated_dir = os.path.join(results_dir, "generated_images/")
os.makedirs(generated_dir, exist_ok=True)

TOP_K = 5  # Number of images to retrieve per article

# ===================================
# Load datasets
# ===================================
subset_columns = ["article_id", "article_url", "article_title", "article_tags", "image_id", "image_url"]

df_full = pd.read_csv(os.path.join(base_path, "newsarticles.csv"))
df_subset = pd.read_csv(os.path.join(base_path, "subset.csv"), header=None, names=subset_columns)

print("✅ Loaded datasets")
print("Full dataset shape:", df_full.shape)
print("Subset dataset shape:", df_subset.shape)

# ===================================
# Prepare text for embeddings
# ===================================
df_full["text"] = df_full["article_title"].fillna("") + ". " + df_full["article_tags"].fillna("")

# ===================================
# Load SentenceTransformer
# ===================================
model = SentenceTransformer("all-MiniLM-L6-v2", device=device)

# ===================================
# Generate embeddings
# ===================================
print("⚡ Generating embeddings for full dataset...")
text_embeddings = model.encode(
    df_full["text"].tolist(),
    batch_size=64,
    show_progress_bar=True,
    convert_to_numpy=True,
    device=device
)
text_embeddings = text_embeddings / np.linalg.norm(text_embeddings, axis=1, keepdims=True)

# ===================================
# Build FAISS index (GPU if available)
# ===================================
d = text_embeddings.shape[1]
cpu_index = faiss.IndexFlatIP(d)

if device == "cuda":
    res = faiss.StandardGpuResources()
    index = faiss.index_cpu_to_gpu(res, 0, cpu_index)
else:
    index = cpu_index

index.add(text_embeddings)
print("✅ FAISS index built with:", index.ntotal, "articles (on", device, ")")

# ===================================
# Retrieval function
# ===================================
def retrieve_top_k(df_queries, top_k=TOP_K):
    results = []
    for i, row in tqdm(df_queries.iterrows(), total=len(df_queries), desc="Retrieving"):
        query_text = str(row["article_title"]) + ". " + str(row["article_tags"])
        q_emb = model.encode([query_text], convert_to_numpy=True, device=device)
        q_emb = q_emb / np.linalg.norm(q_emb, axis=1, keepdims=True)
        D, I = index.search(q_emb, top_k)
        for rank, idx in enumerate(I[0]):
            retrieved = df_full.iloc[idx]
            results.append({
                "query_article_id": row["article_id"],
                "query_title": row["article_title"],
                "retrieved_article_id": retrieved["article_id"],
                "retrieved_article_title": retrieved["article_title"],
                "retrieved_image_id": retrieved["image_id"],
                "retrieved_image_url": retrieved["image_url"],
                "score": float(D[0][rank]),
                "rank": rank + 1
            })
    return pd.DataFrame(results)

# ===================================
# Task 1a: Retrieve for subset
# ===================================
print("⚡ Retrieving images for subset...")
df_subset_results = retrieve_top_k(df_subset, top_k=TOP_K)
subset_out = os.path.join(results_dir, "task1_subset_results.csv")
df_subset_results.to_csv(subset_out, index=False)
print("✅ Subset retrieval results saved:", subset_out)

# ===================================
# Task 1b: Retrieve for full dataset
# ===================================
print("⚡ Retrieving images for full dataset...")
df_full_results = retrieve_top_k(df_full, top_k=TOP_K)
full_out = os.path.join(results_dir, "task1_full_dataset_results.csv")
df_full_results.to_csv(full_out, index=False)
print("✅ Full dataset retrieval results saved:", full_out)



Mounted at /content/drive
⚡ Using device: cuda
✅ Loaded datasets
Full dataset shape: (8500, 6)
Subset dataset shape: (30, 6)


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

...

✅ FAISS index built with: 8500 articles (on cuda )
⚡ Retrieving images for subset...


Retrieving: 100%|██████████| 30/30 [00:00<00:00, 78.07it/s]


✅ Subset retrieval results saved: /content/drive/MyDrive/MediaEval/newsimages_25_v1.1/results_local/task1_subset_results.csv
⚡ Retrieving images for full dataset...


Retrieving: 100%|██████████| 8500/8500 [01:05<00:00, 129.59it/s]


✅ Full dataset retrieval results saved: /content/drive/MyDrive/MediaEval/newsimages_25_v1.1/results_local/task1_full_dataset_results.csv


In [ ]:
# ===================================
# Task 2: Stable Diffusion (GPU optimized)
# ===================================
print("⚡ Setting up Stable Diffusion for local generation...")
model_name = "runwayml/stable-diffusion-v1-5"
scheduler = EulerDiscreteScheduler.from_pretrained(model_name, subfolder="scheduler")

pipe = StableDiffusionPipeline.from_pretrained(
    model_name,
    scheduler=scheduler,
    torch_dtype=torch.float16 if device == "cuda" else torch.float32
)
pipe = pipe.to(device)

if device == "cuda":
    pipe.enable_attention_slicing()

def generate_image_local(prompt, save_path, num_inference_steps=30, guidance_scale=7.5):
    image = pipe(prompt, num_inference_steps=num_inference_steps, guidance_scale=guidance_scale).images[0]
    image.save(save_path)

# ===================================
# Generate images for subset
# ===================================
generated_data = []
print("⚡ Generating images for subset locally...")
for i, row in tqdm(df_subset.iterrows(), total=len(df_subset), desc="Generating images"):
    prompt = f"{row['article_title']}. {row['article_tags']}. Illustration, non-photorealistic, news thumbnail."
    save_path = os.path.join(generated_dir, f"{row['article_id']}.png")
    try:
        generate_image_local(prompt, save_path)
        generated_data.append({
            "article_id": row["article_id"],
            "article_title": row["article_title"],
            "image_path": save_path,
            "prompt": prompt
        })
    except Exception as e:
        print(f"❌ Failed to generate image for article {row['article_id']}: {e}")

# Save metadata
df_generated = pd.DataFrame(generated_data)
gen_csv = os.path.join(generated_dir, "task2_generated_images_local.csv")
df_generated.to_csv(gen_csv, index=False)
print("✅ Generated images metadata saved:", gen_csv)

# ===============================
# Image Generation for FULL dataset
# ===============================
print("⚡ Generating images for full dataset...")

generated_data_full = []

for i, row in tqdm(df_full.iterrows(), total=len(df_full), desc="Generating full dataset"):
    prompt = f"{row['article_title']}. {row['article_tags']}. Illustration, non-photorealistic, news thumbnail."
    save_path = os.path.join(generated_dir, f"{row['article_id']}.png")

    try:
        generate_image_local(prompt, save_path)
        generated_data_full.append({
            "article_id": row["article_id"],
            "article_title": row["article_title"],
            "image_path": save_path,
            "prompt": prompt
        })
    except Exception as e:
        print(f"❌ Failed to generate image for article {row['article_id']}: {e}")

# Save metadata
df_generated_full = pd.DataFrame(generated_data_full)
gen_csv_full = os.path.join(generated_dir, "task2_generated_images_full.csv")
df_generated_full.to_csv(gen_csv_full, index=False)
print("✅ Generated FULL dataset images metadata saved:", gen_csv_full)



⚡ Setting up Stable Diffusion for local generation...


scheduler_config.json:   0%|          | 0.00/308 [00:00<?, ?B/s]

model_index.json:   0%|          | 0.00/541 [00:00<?, ?B/s]

Fetching 14 files:   0%|          | 0/14 [00:00<?, ?it/s]

preprocessor_config.json:   0%|          | 0.00/342 [00:00<?, ?B/s]

...

  0%|          | 0/30 [00:00<?, ?it/s]

Generating full dataset:   7%|▋         | 635/8500 [1:10:42<14:34:32,  6.67s/it]

  0%|          | 0/30 [00:00<?, ?it/s]

Generating full dataset:   7%|▋         | 636/8500 [1:10:48<14:33:20,  6.66s/it]

  0%|          | 0/30 [00:00<?, ?it/s]

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from tqdm import tqdm
from transformers import CLIPProcessor, CLIPModel
from PIL import Image
import torch

# ===============================
# Retrieval Metrics Function
# ===============================
def evaluate_retrieval(df_results, df_queries, top_k=5, return_all=False):
    metrics = {"precision_at_k": [], "recall_at_k": [], "mrr": [], "ndcg": []}

    for qid in df_queries["article_id"]:
        q_results = df_results[df_results["query_article_id"] == qid]
        gt_image = df_queries[df_queries["article_id"] == qid]["image_id"].values[0]

        ranks = q_results[q_results["retrieved_image_id"] == gt_image]["rank"].values

        if len(ranks) > 0:
            rank = ranks[0]
            prec_at_k = np.mean(q_results.head(top_k)["retrieved_image_id"] == gt_image)
            rec_at_k = 1.0 if rank <= top_k else 0.0
            rr = 1.0 / rank
            ndcg = 1.0 / np.log2(rank + 1)
        else:
            prec_at_k, rec_at_k, rr, ndcg = 0, 0, 0, 0

        metrics["precision_at_k"].append(prec_at_k)
        metrics["recall_at_k"].append(rec_at_k)
        metrics["mrr"].append(rr)
        metrics["ndcg"].append(ndcg)

    summary = {m: np.mean(v) for m, v in metrics.items()}
    if return_all:
        return summary, metrics
    return summary


# ===============================
# Evaluate Retrieval
# ===============================
retrieval_metrics_subset, retrieval_all_subset = evaluate_retrieval(df_subset_results, df_subset, return_all=True)
retrieval_metrics_full, retrieval_all_full = evaluate_retrieval(df_full_results, df_full, return_all=True)

print("✅ Retrieval Metrics (Subset):", retrieval_metrics_subset)
print("✅ Retrieval Metrics (Full):", retrieval_metrics_full)


# ===============================
# Load CLIP Model for Generation Evaluation
# ===============================
device = "cuda" if torch.cuda.is_available() else "cpu"
print("⚡ Using device:", device)

clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32").to(device)
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")


def compute_clip_score(df_generated, return_all=False):
    scores = []
    for _, row in tqdm(df_generated.iterrows(), total=len(df_generated), desc="CLIP scoring"):
        try:
            image = Image.open(row["image_path"]).convert("RGB")
            inputs = clip_processor(
                text=[row["article_title"]],
                images=image,
                return_tensors="pt",
                padding=True
            ).to(device)
            outputs = clip_model(**inputs)
            score = outputs.logits_per_image.item()
            scores.append(score)
        except Exception as e:
            print(f"⚠️ Error scoring {row['article_id']}: {e}")
            scores.append(0.0)

    avg_score = np.mean(scores)
    if return_all:
        return avg_score, scores
    return avg_score


# ===============================
# Compute CLIP Scores
# ===============================
clip_score_subset, clip_scores_subset = compute_clip_score(df_generated, return_all=True)
clip_score_full, clip_scores_full = compute_clip_score(df_generated_full, return_all=True)

print(f"✅ Avg CLIP Score (Subset): {clip_score_subset:.4f}")
print(f"✅ Avg CLIP Score (Full): {clip_score_full:.4f}")


# ===============================
# Visualization
# ===============================
# 1. Retrieval Metrics Comparison
metrics_df = pd.DataFrame([
    {"Dataset": "Subset", **retrieval_metrics_subset},
    {"Dataset": "Full", **retrieval_metrics_full}
])

plt.figure(figsize=(8,6))
metrics_df.set_index("Dataset").plot(kind="bar", rot=0)
plt.title("Retrieval Metrics Comparison")
plt.ylabel("Score")
plt.ylim(0, 1.1)
plt.legend(title="Metric")
plt.grid(axis="y", linestyle="--", alpha=0.7)
plt.show()

# 2. CLIP Score Comparison
plt.figure(figsize=(6,4))
plt.bar(["Subset", "Full"], [clip_score_subset, clip_score_full], color=["skyblue", "lightgreen"])
plt.title("Average CLIP Score for Generated Images")
plt.ylabel("CLIP Score")
plt.ylim(0, max(clip_score_subset, clip_score_full) + 1)
plt.grid(axis="y", linestyle="--", alpha=0.7)
plt.show()


# ===============================
# 🔹 NEW: Variance & Distribution Analysis
# ===============================
# Retrieval Variance
for dataset_name, metrics_all in [("Subset", retrieval_all_subset), ("Full", retrieval_all_full)]:
    print(f"\n📊 Retrieval Variance ({dataset_name})")
    for m, values in metrics_all.items():
        print(f"{m}: mean={np.mean(values):.4f}, var={np.var(values):.4f}, std={np.std(values):.4f}")

    # Boxplot
    plt.figure(figsize=(7,5))
    plt.boxplot(metrics_all.values(), labels=metrics_all.keys())
    plt.title(f"Retrieval Metric Distributions - {dataset_name}")
    plt.ylabel("Score")
    plt.grid(axis="y", linestyle="--", alpha=0.7)
    plt.show()

# CLIP Score Distributions
for dataset_name, scores in [("Subset", clip_scores_subset), ("Full", clip_scores_full)]:
    print(f"\n📊 CLIP Score Stats ({dataset_name})")
    print(f"mean={np.mean(scores):.4f}, var={np.var(scores):.4f}, std={np.std(scores):.4f}, min={np.min(scores):.4f}, max={np.max(scores):.4f}")

    plt.figure(figsize=(7,5))
    plt.hist(scores, bins=30, color="skyblue", edgecolor="black", alpha=0.7)
    plt.title(f"CLIP Score Distribution - {dataset_name}")
    plt.xlabel("CLIP Score")
    plt.ylabel("Frequency")
    plt.grid(axis="y", linestyle="--", alpha=0.7)
    plt.show()
